## Download PM2.5 Hourly Data for Weather Stations

In [4]:
import requests
import os
import time

In [ ]:
# programatically download both federally-regulated and non-federally-regulated PM2.5 information
# https://aqs.epa.gov/aqsweb/airdata/download_files.html#Raw
years = list(range(2010,2024+1))
if not os.path.exists("PM2.5"):
    os.mkdir("PM2.5")
for year in years:
    print(year)
    if not os.path.exists(f"PM2.5/hourly_88101_{year}.zip"):
        url = f"https://aqs.epa.gov/aqsweb/airdata/hourly_88101_{year}.zip"
        response = requests.get(url, stream=True)
        with open(f"PM2.5/hourly_88101_{year}.zip", mode="wb") as file:
            for chunk in response.iter_content(chunk_size=10 * 1024):
                file.write(chunk)

    if not os.path.exists(f"PM2.5/hourly_88502_{year}.zip"):
        url = f"https://aqs.epa.gov/aqsweb/airdata/hourly_88502_{year}.zip"
        response = requests.get(url, stream=True)
        with open(f"PM2.5/hourly_88502_{year}.zip", mode="wb") as file:
            for chunk in response.iter_content(chunk_size=10 * 1024):
                file.write(chunk)
        time.sleep(2)
    

In [ ]:
import pandas as pd
PM2010 = pd.read_csv('PM2.5/hourly_88101_2010.zip')
PM2010

In [ ]:
PM2010_88502 = pd.read_csv('PM2.5/hourly_88502_2010.zip')
PM2010_88502

## Other Weather Station Data (meteostat)

In [ ]:
# download bulk meteostat data
if not os.path.exists("meteostat/bulk_data_full.json.gz"):
    url = "https://bulk.meteostat.net/v2/stations/full.json.gz"
    response = requests.get(url, stream=True)
    if not os.path.exists("meteostat"):
        os.mkdir("meteostat")
        with open("meteostat/bulk_data_full.json.gz", mode="wb") as file:
            for chunk in response.iter_content(chunk_size=10 * 1024):
                file.write(chunk)


In [ ]:
import json
import gzip
# with open('meteostat/bulk_data_full.json.gz', 'r') as file:
#     full = json.load(file)

with gzip.open('meteostat/bulk_data_full.json.gz', 'r') as fin:
    full = json.loads(fin.read().decode('utf-8'))
usStations = [x for x in full if x["country"] == "US"]
usStations[0:3]

In [ ]:
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point

# radius for matching
radius = 100

# Convert DataFrames to GeoDataFrames
def to_gdf(df, lat_col='latitude', lon_col='longitude'):
    geometry = [Point(xy) for xy in zip(df[lon_col], df[lat_col])]
    return gpd.GeoDataFrame(df, geometry=geometry, crs="EPSG:4326")

# add geometry column for long/lat comparisons
PM2010geo = to_gdf(PM2010, 'Latitude', 'Longitude')
PM2010_88502geo = to_gdf(PM2010_88502, 'Latitude', 'Longitude')

In [ ]:
# convert json to dataframe
usStationsdf = pd.DataFrame(usStations)
usStationsdf

In [ ]:
# extract lat long from table
usStationsdf['latitude'] = [x['latitude'] for x in usStationsdf['location']]
usStationsdf['longitude'] = [x['longitude'] for x in usStationsdf['location']]

In [ ]:
display(usStationsdf[['latitude', 'longitude']])
display(PM2010geo.drop_duplicates(('Latitude', 'Longitude'))[['Latitude', 'Longitude']])

In [ ]:
# usStationsdf['latitude'] = round(usStationsdf['latitude'], 2)
# usStationsdf['longitude'] = round(usStationsdf['longitude'], 2)

# PM2010geo['Latitude'] = round(PM2010geo['Latitude'], 2)
# PM2010geo['Longitude'] = round(PM2010geo['Longitude'], 2)

# display(usStationsdf[['latitude', 'longitude']])
# display(PM2010geo.drop_duplicates(('Latitude', 'Longitude'))[['Latitude', 'Longitude']])

In [ ]:
# usStationsdf.merge(PM2010geo.drop_duplicates(('Latitude', 'Longitude')), left_on=('latitude', 'longitude'), right_on=('Latitude', 'Longitude'))

In [ ]:
# add geometry column for long/lat comparisons
usStationsgeo = to_gdf(usStationsdf)

In [ ]:
# project to mercator for meter comparisons
PM2010geo = PM2010geo.to_crs(epsg=3857)
PM2010_88502geo = PM2010_88502geo.to_crs(epsg=3857)
usStationsgeo = usStationsgeo.to_crs(epsg=3857)

In [ ]:
display(PM2010geo.shape)
display(PM2010_88502geo.shape)
display(usStationsgeo.shape)

In [ ]:
display(PM2010geo['geometry'])
display(PM2010_88502geo['geometry'])
display(usStationsgeo['geometry'])

In [ ]:
m = PM2010geo.drop_duplicates(('Latitude', 'Longitude')).explore()
m = PM2010_88502geo.drop_duplicates(('Latitude', 'Longitude')).explore(m = m, color='green')
usStationsgeo.explore(m=m, color='red')

# Same, but 2024

In [5]:
import pandas as pd
PM2024 = pd.read_csv('PM2.5/hourly_88101_2024.zip')
PM2024

/tmp/ipykernel_23998/2549592291.py:2: DtypeWarning: Columns (17) have mixed types. Specify dtype option on import or set low_memory=False.
  PM2024 = pd.read_csv('PM2.5/hourly_88101_2024.zip')


State Code  County Code  Site Num  Parameter Code  POC   Latitude  \
0                 1            3        10           88101    3  30.497478   
1                 1            3        10           88101    3  30.497478   
2                 1            3        10           88101    3  30.497478   
3                 1            3        10           88101    3  30.497478   
4                 1            3        10           88101    3  30.497478   
...             ...          ...       ...             ...  ...        ...   
4759889          80           26         6           88101    1  31.291293   
4759890          80           26         6           88101    1  31.291293   
4759891          80           26         6           88101    1  31.291293   
4759892          80           26         6           88101    1  31.291293   
4759893          80           26         6           88101    1  31.291293   

          Longitude  Datum            Parameter Name  Date Local  ...  \
0        -87.880258  NAD83  PM2.5 - Local Conditions  2024-01-02  ...   
1        -87.880258  NAD83  PM2.5 - Local Conditions  2024-01-02  ...   
2        -87.880258  NAD83  PM2.5 - Local Conditions  2024-01-02  ...   
3        -87.880258  NAD83  PM2.5 - Local Conditions  2024-01-02  ...   
4        -87.880258  NAD83  PM2.5 - Local Conditions  2024-01-02  ...   
...             ...    ...                       ...         ...  ...   
4759889 -110.951513  WGS84  PM2.5 - Local Conditions  2024-09-30  ...   
4759890 -110.951513  WGS84  PM2.5 - Local Conditions  2024-09-30  ...   
4759891 -110.951513  WGS84  PM2.5 - Local Conditions  2024-09-30  ...   
4759892 -110.951513  WGS84  PM2.5 - Local Conditions  2024-09-30  ...   
4759893 -110.951513  WGS84  PM2.5 - Local Conditions  2024-09-30  ...   

                    Units of Measure  MDL Uncertainty  Qualifier Method Type  \
0        Micrograms/cubic meter (LC)  5.0         NaN        NaN         FEM   
1        Micrograms/cubic meter (LC)  5.0         NaN        NaN         FEM   
2        Micrograms/cubic meter (LC)  5.0         NaN        NaN         FEM   
3        Micrograms/cubic meter (LC)  5.0         NaN        NaN         FEM   
4        Micrograms/cubic meter (LC)  5.0         NaN        NaN         FEM   
...                              ...  ...         ...        ...         ...   
4759889  Micrograms/cubic meter (LC)  0.1         NaN        NaN         FEM   
4759890  Micrograms/cubic meter (LC)  0.1         NaN        NaN         FEM   
4759891  Micrograms/cubic meter (LC)  0.1         NaN        NaN         FEM   
4759892  Micrograms/cubic meter (LC)  0.1         NaN        NaN         FEM   
4759893  Micrograms/cubic meter (LC)  0.1         NaN        NaN         FEM   

         Method Code                                        Method Name  \
0                209  Met One BAM-1022 Mass Monitor w/ VSCC or TE-PM...   
1                209  Met One BAM-1022 Mass Monitor w/ VSCC or TE-PM...   
2                209  Met One BAM-1022 Mass Monitor w/ VSCC or TE-PM...   
3                209  Met One BAM-1022 Mass Monitor w/ VSCC or TE-PM...   
4                209  Met One BAM-1022 Mass Monitor w/ VSCC or TE-PM...   
...              ...                                                ...   
4759889          638  Teledyne T640X at 16.67 LPM w/Network Data Ali...   
4759890          638  Teledyne T640X at 16.67 LPM w/Network Data Ali...   
4759891          638  Teledyne T640X at 16.67 LPM w/Network Data Ali...   
4759892          638  Teledyne T640X at 16.67 LPM w/Network Data Ali...   
4759893          638  Teledyne T640X at 16.67 LPM w/Network Data Ali...   

                State Name County Name  Date of Last Change  
0                  Alabama     Baldwin           2024-07-19  
1                  Alabama     Baldwin           2024-07-19  
2                  Alabama     Baldwin           2024-07-19  
3                  Alabama     Baldwin           2024-07-19  
4                  Alab

In [6]:
PM2024_88502 = pd.read_csv('PM2.5/hourly_88502_2024.zip')
PM2024_88502

/tmp/ipykernel_23998/4163065550.py:1: DtypeWarning: Columns (17) have mixed types. Specify dtype option on import or set low_memory=False.
  PM2024_88502 = pd.read_csv('PM2.5/hourly_88502_2024.zip')


State Code  County Code  Site Num  Parameter Code  POC   Latitude  \
0                 2          110         4           88502    3  58.388497   
1                 2          110         4           88502    3  58.388497   
2                 2          110         4           88502    3  58.388497   
3                 2          110         4           88502    3  58.388497   
4                 2          110         4           88502    3  58.388497   
...             ...          ...       ...             ...  ...        ...   
1042870          72           97         7           88502    1  18.216038   
1042871          72           97         7           88502    1  18.216038   
1042872          72           97         7           88502    1  18.216038   
1042873          72           97         7           88502    1  18.216038   
1042874          72           97         7           88502    1  18.216038   

          Longitude  Datum                          Parameter Name  \
0       -134.567237  WGS84  Acceptable PM2.5 AQI & Speciation Mass   
1       -134.567237  WGS84  Acceptable PM2.5 AQI & Speciation Mass   
2       -134.567237  WGS84  Acceptable PM2.5 AQI & Speciation Mass   
3       -134.567237  WGS84  Acceptable PM2.5 AQI & Speciation Mass   
4       -134.567237  WGS84  Acceptable PM2.5 AQI & Speciation Mass   
...             ...    ...                                     ...   
1042870  -67.144107  NAD83  Acceptable PM2.5 AQI & Speciation Mass   
1042871  -67.144107  NAD83  Acceptable PM2.5 AQI & Speciation Mass   
1042872  -67.144107  NAD83  Acceptable PM2.5 AQI & Speciation Mass   
1042873  -67.144107  NAD83  Acceptable PM2.5 AQI & Speciation Mass   
1042874  -67.144107  NAD83  Acceptable PM2.5 AQI & Speciation Mass   

         Date Local  ...             Units of Measure  MDL Uncertainty  \
0        2024-01-01  ...  Micrograms/cubic meter (LC)  0.1         NaN   
1        2024-01-01  ...  Micrograms/cubic meter (LC)  0.1         NaN   
2        2024-01-01  ...  Micrograms/cubic meter (LC)  0.1         NaN   
3        2024-01-01  ...  Micrograms/cubic meter (LC)  0.1         NaN   
4        2024-01-01  ...  Micrograms/cubic meter (LC)  0.1         NaN   
...             ...  ...                          ...  ...         ...   
1042870  2024-06-30  ...  Micrograms/cubic meter (LC)  2.0         NaN   
1042871  2024-06-30  ...  Micrograms/cubic meter (LC)  2.0         NaN   
1042872  2024-06-30  ...  Micrograms/cubic meter (LC)  2.0         NaN   
1042873  2024-06-30  ...  Micrograms/cubic meter (LC)  2.0         NaN   
1042874  2024-06-30  ...  Micrograms/cubic meter (LC)  2.0         NaN   

         Qualifier Method Type  Method Code  \
0               IH         FEM          238   
1               IH         FEM          238   
2               IH         FEM          238   
3               IH         FEM          238   
4               IH         FEM          238   
...            ...         ...          ...   
1042870          V     Non-FRM          181   
1042871        NaN     Non-FRM          181   
1042872        NaN     Non-FRM          181   
1042873        NaN     Non-FRM          181   
1042874        NaN     Non-FRM          181   

                                               Method Name   State Name  \
0        Teledyne T640X at 16.67 LPM - Broadband spectr...       Alaska   
1        Teledyne T640X at 16.67 LPM - Broadband spectr...       Alaska   
2        Teledyne T640X at 16.67 LPM - Broadband spectr...       Alaska   
3        Teledyne T640X at 16.67 LPM - Broadband spectr...       Alaska   
4        Teledyne T640X at 16.67 LPM - Broadband spectr...       Alaska   
...                                                    ...          ...   
1042870                      PM2.5 VSCC - FDMS-Gravimetric  Puerto Rico   
1042871                      PM2.5 VSCC - FDMS-Gravimetric  Puerto Rico   
1042872                      PM2.5 VSCC - FDMS-Gravimetric  Puerto Rico   
1042873                    

## Other Weather Station Data (meteostat)

In [7]:
# download bulk meteostat data
if not os.path.exists("meteostat/bulk_data_full.json.gz"):
    url = "https://bulk.meteostat.net/v2/stations/full.json.gz"
    response = requests.get(url, stream=True)
    if not os.path.exists("meteostat"):
        os.mkdir("meteostat")
        with open("meteostat/bulk_data_full.json.gz", mode="wb") as file:
            for chunk in response.iter_content(chunk_size=10 * 1024):
                file.write(chunk)


In [8]:
import json
import gzip
# with open('meteostat/bulk_data_full.json.gz', 'r') as file:
#     full = json.load(file)

with gzip.open('meteostat/bulk_data_full.json.gz', 'r') as fin:
    full = json.loads(fin.read().decode('utf-8'))
usStations = [x for x in full if x["country"] == "US"]
usStations[0:3]

[{'id': '04AEH',
  'name': {'en': 'Norwich'},
  'country': 'US',
  'region': 'NY',
  'identifiers': {'national': None, 'wmo': None, 'icao': 'KOIC'},
  'location': {'latitude': 42.5665, 'longitude': -75.5242, 'elevation': 312},
  'timezone': 'America/New_York',
  'inventory': {'model': {'start': '2022-04-24', 'end': '2025-04-23'},
   'hourly': {'start': '2022-04-23', 'end': '2025-04-14'},
   'daily': {'start': '2022-04-23', 'end': '2022-04-26'},
   'monthly': {'start': None, 'end': None},
   'normals': {'start': None, 'end': None}}},
 {'id': '0MV8M',
  'name': {'en': 'Hill Air Force Base'},
  'country': 'US',
  'region': 'UT',
  'identifiers': {'national': None, 'wmo': None, 'icao': 'KHIF'},
  'location': {'latitude': 41.1111, 'longitude': -111.9623, 'elevation': 1459},
  'timezone': 'America/Denver',
  'inventory': {'model': {'start': '2022-04-24', 'end': '2025-04-23'},
   'hourly': {'start': '2022-04-23', 'end': '2025-04-14'},
   'daily': {'start': '2022-04-23', 'end': '2022-04-25'},


In [9]:
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point

# radius for matching
radius = 100

# Convert DataFrames to GeoDataFrames
def to_gdf(df, lat_col='latitude', lon_col='longitude'):
    geometry = [Point(xy) for xy in zip(df[lon_col], df[lat_col])]
    return gpd.GeoDataFrame(df, geometry=geometry, crs="EPSG:4326")

# add geometry column for long/lat comparisons
PM2024geo = to_gdf(PM2024, 'Latitude', 'Longitude')
PM2024_88502geo = to_gdf(PM2024_88502, 'Latitude', 'Longitude')

In [10]:
# convert json to dataframe
usStationsdf = pd.DataFrame(usStations)
usStationsdf

id                                         name country region  \
0     04AEH                            {'en': 'Norwich'}      US     NY   
1     0MV8M                {'en': 'Hill Air Force Base'}      US     UT   
2     0NNEW  {'en': 'Effingham County Memorial Airport'}      US     IL   
3     0OBKP            {'en': 'Live Oak County Airport'}      US     TX   
4     0RJDR                     {'en': 'Hotel (Gurley)'}      US     NE   
...     ...                                          ...     ...    ...   
2930  ZGK9P                {'en': 'Victorville Airport'}      US     CA   
2931  ZJ8AR                     {'en': 'India - Sidney'}      US     NE   
2932  ZNWZW         {'en': 'Columbus Municipal Airport'}      US     NE   
2933  ZUQJS          {'en': 'Ephraim-Gibraltar Airport'}      US     WI   
2934  ZYITU  {'en': 'Selfridge Air National Guard Base'}      US     MI   

                                          identifiers  \
0     {'national': None, 'wmo': None, 'icao': 'KOIC'}   
1     {'national': None, 'wmo': None, 'icao': 'KHIF'}   
2     {'national': None, 'wmo': None, 'icao': 'K1H2'}   
3     {'national': None, 'wmo': None, 'icao': 'K8T6'}   
4     {'national': None, 'wmo': None, 'icao': 'K1HW'}   
...                                               ...   
2930  {'national': None, 'wmo': None, 'icao': 'KVCV'}   
2931  {'national': None, 'wmo': None, 'icao': 'K1IW'}   
2932  {'national': None, 'wmo': None, 'icao': 'KOLU'}   
2933  {'national': None, 'wmo': None, 'icao': 'K3D2'}   
2934  {'national': None, 'wmo': None, 'icao': 'KMTC'}   

                                               location             timezone  \
0     {'latitude': 42.5665, 'longitude': -75.5242, '...     America/New_York   
1     {'latitude': 41.1111, 'longitude': -111.9623, ...       America/Denver   
2     {'latitude': 39.0706, 'longitude': -88.5333, '...      America/Chicago   
3     {'latitude': 28.3628, 'longitude': -98.1165, '...      America/Chicago   
4     {'latitude': 41.32, 'longitude': -102.83, 'ele...       America/Denver   
...                                                 ...                  ...   
2930  {'latitude': 34.5972, 'longitude': -117.3828, ...  America/Los_Angeles   
2931  {'latitude': 41.05, 'longitude': -102.87, 'ele...       America/Denver   
2932  {'latitude': 41.45, 'longitude': -97.3333, 'el...      America/Chicago   
2933  {'latitude': 45.1357, 'longitude': -87.1881, '...    America/Menominee   
2934  {'latitude': 42.6046, 'longitude': -82.8353, '...      America/Detroit   

                                              inventory  
0     {'model': {'start': '2022-04-24', 'end': '2025...  
1     {'model': {'start': '2022-04-24', 'end': '2025...  
2     {'model': {'start': '2022-05-07', 'end': '2025...  
3     {'model': {'start': '2022-05-06', 'end': '2025...  
4     {'model': {'start': '2022-05-07', 'end': '2025...  
...                                                 ...  
2930  {'model': {'start': '2022-04-24', 'end': '2025...  
2931  {'model': {'start': '2022-05-07', 'end': '2025...  
2932  {'model': {'start': '2022-04-24', 'end': '2025...  
2933  {'model': {'start': '2022-05-07', 'end': '2025...  
2934  {'model': {'start': '2022-04-24', 'end': '2025...  

[2935 rows x 8 columns]

In [11]:
# extract lat long from table
usStationsdf['latitude'] = [x['latitude'] for x in usStationsdf['location']]
usStationsdf['longitude'] = [x['longitude'] for x in usStationsdf['location']]

In [12]:
display(usStationsdf[['latitude', 'longitude']])
display(PM2024geo.drop_duplicates(('Latitude', 'Longitude'))[['Latitude', 'Longitude']])

latitude  longitude
0      42.5665   -75.5242
1      41.1111  -111.9623
2      39.0706   -88.5333
3      28.3628   -98.1165
4      41.3200  -102.8300
...        ...        ...
2930   34.5972  -117.3828
2931   41.0500  -102.8700
2932   41.4500   -97.3333
2933   45.1357   -87.1881
2934   42.6046   -82.8353

[2935 rows x 2 columns]

Latitude   Longitude
0        30.497478  -87.880258
4114     33.284928  -85.803608
9181     34.288567  -85.969858
14048    33.988210  -85.992556
19113    34.685470  -86.588160
...            ...         ...
4735300  43.457760 -110.797990
4740194  44.373056 -110.830833
4745899  44.007919 -107.956965
4750123  18.420089  -66.150615
4753364  31.291293 -110.951513

[880 rows x 2 columns]

In [13]:
# usStationsdf['latitude'] = round(usStationsdf['latitude'], 2)
# usStationsdf['longitude'] = round(usStationsdf['longitude'], 2)

# PM2024geo['Latitude'] = round(PM2024geo['Latitude'], 2)
# PM2024geo['Longitude'] = round(PM2024geo['Longitude'], 2)

# display(usStationsdf[['latitude', 'longitude']])
# display(PM2024geo.drop_duplicates(('Latitude', 'Longitude'))[['Latitude', 'Longitude']])

In [14]:
# usStationsdf.merge(PM2024geo.drop_duplicates(('Latitude', 'Longitude')), left_on=('latitude', 'longitude'), right_on=('Latitude', 'Longitude'))

In [15]:
# add geometry column for long/lat comparisons
usStationsgeo = to_gdf(usStationsdf)

In [16]:
# project to mercator for meter comparisons
PM2024geo = PM2024geo.to_crs(epsg=3857)
PM2024_88502geo = PM2024_88502geo.to_crs(epsg=3857)
usStationsgeo = usStationsgeo.to_crs(epsg=3857)

In [17]:
display(PM2024geo.shape)
display(PM2024_88502geo.shape)
display(usStationsgeo.shape)

(4759894, 25)

(1042875, 25)

(2935, 11)

In [18]:
display(PM2024geo['geometry'])
display(PM2024_88502geo['geometry'])
display(usStationsgeo['geometry'])

0           POINT (-9782785.571 3567657.627)
1           POINT (-9782785.571 3567657.627)
2           POINT (-9782785.571 3567657.627)
3           POINT (-9782785.571 3567657.627)
4           POINT (-9782785.571 3567657.627)
                         ...                
4759889    POINT (-12351065.930 3670637.147)
4759890    POINT (-12351065.930 3670637.147)
4759891    POINT (-12351065.930 3670637.147)
4759892    POINT (-12351065.930 3670637.147)
4759893    POINT (-12351065.930 3670637.147)
Name: geometry, Length: 4759894, dtype: geometry

0          POINT (-14979956.300 8049375.275)
1          POINT (-14979956.300 8049375.275)
2          POINT (-14979956.300 8049375.275)
3          POINT (-14979956.300 8049375.275)
4          POINT (-14979956.300 8049375.275)
                         ...                
1042870     POINT (-7474447.801 2062850.975)
1042871     POINT (-7474447.801 2062850.975)
1042872     POINT (-7474447.801 2062850.975)
1042873     POINT (-7474447.801 2062850.975)
1042874     POINT (-7474447.801 2062850.975)
Name: geometry, Length: 1042875, dtype: geometry

0        POINT (-8407315.487 5246219.783)
1       POINT (-12463586.224 5028742.725)
2        POINT (-9855481.874 4731789.468)
3       POINT (-10922278.818 3294792.050)
4       POINT (-11446983.238 5059656.788)
                      ...                
2930    POINT (-13066993.524 4109276.073)
2931    POINT (-11451436.018 5019719.452)
2932    POINT (-10835093.393 5078944.869)
2933     POINT (-9705734.895 5642910.032)
2934     POINT (-9221183.416 5251980.286)
Name: geometry, Length: 2935, dtype: geometry

In [19]:
m = PM2024geo.drop_duplicates(('Latitude', 'Longitude')).explore()
m = PM2024_88502geo.drop_duplicates(('Latitude', 'Longitude')).explore(m = m, color='green')
usStationsgeo.explore(m=m, color='red')

In [28]:
cmaq = pd.read_csv('cmaq_grid.csv')
cmaq.describe()

Col            Row            Lon            Lat  \
count  137236.000000  137236.000000  137236.000000  137236.000000   
mean      229.991657     149.994644     -94.704555      39.076362   
std       132.497259      86.310708      18.926220       9.196761   
min         1.000000       1.000000    -134.389010      20.663460   
25%       115.000000      75.000000    -110.929090      31.151220   
50%       230.000000     150.000000     -94.644305      39.075450   
75%       345.000000     225.000000     -78.508670      46.963800   
max       459.000000     299.000000     -54.717560      56.473930   

                Conc  
count  137236.000000  
mean        3.845746  
std         3.732572  
min         0.013718  
25%         1.421382  
50%         2.643770  
75%         4.769837  
max       106.902000

In [38]:
list(range(0, 10000, 46))

[0,
 46,
 92,
 138,
 184,
 230,
 276,
 322,
 368,
 414,
 460,
 506,
 552,
 598,
 644,
 690,
 736,
 782,
 828,
 874,
 920,
 966,
 1012,
 1058,
 1104,
 1150,
 1196,
 1242,
 1288,
 1334,
 1380,
 1426,
 1472,
 1518,
 1564,
 1610,
 1656,
 1702,
 1748,
 1794,
 1840,
 1886,
 1932,
 1978,
 2024,
 2070,
 2116,
 2162,
 2208,
 2254,
 2300,
 2346,
 2392,
 2438,
 2484,
 2530,
 2576,
 2622,
 2668,
 2714,
 2760,
 2806,
 2852,
 2898,
 2944,
 2990,
 3036,
 3082,
 3128,
 3174,
 3220,
 3266,
 3312,
 3358,
 3404,
 3450,
 3496,
 3542,
 3588,
 3634,
 3680,
 3726,
 3772,
 3818,
 3864,
 3910,
 3956,
 4002,
 4048,
 4094,
 4140,
 4186,
 4232,
 4278,
 4324,
 4370,
 4416,
 4462,
 4508,
 4554,
 4600,
 4646,
 4692,
 4738,
 4784,
 4830,
 4876,
 4922,
 4968,
 5014,
 5060,
 5106,
 5152,
 5198,
 5244,
 5290,
 5336,
 5382,
 5428,
 5474,
 5520,
 5566,
 5612,
 5658,
 5704,
 5750,
 5796,
 5842,
 5888,
 5934,
 5980,
 6026,
 6072,
 6118,
 6164,
 6210,
 6256,
 6302,
 6348,
 6394,
 6440,
 6486,
 6532,
 6578,
 6624,
 6670,
 671

In [39]:
to_gdf(cmaq, 'Lat', 'Lon').iloc[list(range(0, 10000, 46)),].explore()

In [ ]:
import matplotlib.pyplot as plt

usStationsgeo.plot()
plt.xlim(-2e7, 0)
plt.ylim(0, 1e7)

In [ ]:
# add Buffer df1 points by 100m
usStationsgeo['geometry'] = usStationsgeo.buffer(1000)

In [ ]:
base = usStationsgeo.plot()
PM2010geonoDup.plot(ax=base)

In [ ]:
# Match all stations within 100m
matches = gpd.sjoin(usStationsgeo, PM2010geonoDup, how='inner', predicate='intersects')
matches